In [ ]:
!pip install sentencepiece
!pip install transformers
!pip install rich[jupyter]

In [ ]:
!pip install datasets
from datasets import load_dataset_builder

ds_builder = load_dataset_builder("multi_news")

In [3]:
from datasets import load_dataset

dataset = load_dataset("multi_news", split="train")

Generating train split:   0%|          | 0/44972 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/5622 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5622 [00:00<?, ? examples/s]

Dataset multi_news downloaded and prepared to /root/.cache/huggingface/datasets/multi_news/default/1.0.0/2f1f69a2bedc8ad1c5d8ae5148e4755ee7095f465c1c01ae8f85454342065a72. Subsequent calls will reuse this data.


In [6]:
import pandas as pd
data = {'text': dataset['document'],
        'summary': dataset['summary']}
df = pd.DataFrame(data)
df = df.sample(14000)

In [8]:
df["text"] = "summarize: "+df["text"]

In [9]:
df.head()

text  \
25643  summarize: A composite sketch of a man suspect...   
33096  summarize: Dave Chappelle is in the midst of a...   
22256  summarize: Meeting Abstracts 2015 Annual Meeti...   
18007  summarize: Story highlights An appeals court s...   
35273  summarize: Funeral likened to hosting World Cu...   

                                                 summary  
25643  – Just a week after 15-year-old Ruby Rubio got...  
33096  – Comedian Dave Chappelle will be hosting Satu...  
22256  – You never know what you'll find on eBay—like...  
18007  – The nation's first execution since Oklahoma'...  
35273  – The death of Nelson Mandela is certain to pl...

In [10]:
# Importing libraries
import os
import numpy as np
import pandas as pd
import torch
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler
import os

# Importing the T5 modules from huggingface/transformers
from transformers import T5Tokenizer, T5ForConditionalGeneration

from rich.table import Column, Table
from rich import box
from rich.console import Console

# define a rich console logger
console=Console(record=True)

def display_df(df):
  """display dataframe in ASCII format"""

  console=Console()
  table = Table(Column("source_text", justify="center" ), Column("target_text", justify="center"), title="Sample Data",pad_edge=False, box=box.ASCII)

  for i, row in enumerate(df.values.tolist()):
    table.add_row(row[0], row[1])

  console.print(table)

training_logger = Table(Column("Epoch", justify="center" ), 
                        Column("Steps", justify="center"),
                        Column("Loss", justify="center"), 
                        title="Training Status",pad_edge=False, box=box.ASCII)


In [11]:
# Setting up the device for GPU usage
from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'

In [12]:
class YourDataSetClass(Dataset):
  """
  Creating a custom dataset for reading the dataset and 
  loading it into the dataloader to pass it to the neural network for finetuning the model

  """

  def __init__(self, dataframe, tokenizer, source_len, target_len, source_text, target_text):
    self.tokenizer = tokenizer
    self.data = dataframe
    self.source_len = source_len
    self.summ_len = target_len
    self.target_text = self.data[target_text]
    self.source_text = self.data[source_text]

  def __len__(self):
    return len(self.target_text)

  def __getitem__(self, index):
    source_text = str(self.source_text[index])
    target_text = str(self.target_text[index])

    #cleaning data so as to ensure data is in string type
    source_text = ' '.join(source_text.split())
    target_text = ' '.join(target_text.split())

    source = self.tokenizer.batch_encode_plus([source_text], max_length= self.source_len, pad_to_max_length=True, truncation=True, padding="max_length", return_tensors='pt')
    target = self.tokenizer.batch_encode_plus([target_text], max_length= self.summ_len, pad_to_max_length=True, truncation=True, padding="max_length", return_tensors='pt')

    source_ids = source['input_ids'].squeeze()
    source_mask = source['attention_mask'].squeeze()
    target_ids = target['input_ids'].squeeze()
    target_mask = target['attention_mask'].squeeze()

    return {
        'source_ids': source_ids.to(dtype=torch.long), 
        'source_mask': source_mask.to(dtype=torch.long), 
        'target_ids': target_ids.to(dtype=torch.long),
        'target_ids_y': target_ids.to(dtype=torch.long)
    }

In [13]:
def train(epoch, tokenizer, model, device, loader, optimizer):

  """
  Function to be called for training with the parameters passed from main function

  """

  model.train()
  for _,data in enumerate(loader, 0):
    y = data['target_ids'].to(device, dtype = torch.long)
    y_ids = y[:, :-1].contiguous()
    lm_labels = y[:, 1:].clone().detach()
    lm_labels[y[:, 1:] == tokenizer.pad_token_id] = -100
    ids = data['source_ids'].to(device, dtype = torch.long)
    mask = data['source_mask'].to(device, dtype = torch.long)

    outputs = model(input_ids = ids, attention_mask = mask, decoder_input_ids=y_ids, labels=lm_labels)
    loss = outputs[0]

    if _%10==0:
      training_logger.add_row(str(epoch), str(_), str(loss))
      console.print(training_logger)

    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

In [14]:
def validate(epoch, tokenizer, model, device, loader):

  """
  Function to evaluate model for predictions

  """
  model.eval()
  predictions = []
  actuals = []
  with torch.no_grad():
      for _, data in enumerate(loader, 0):
          y = data['target_ids'].to(device, dtype = torch.long)
          ids = data['source_ids'].to(device, dtype = torch.long)
          mask = data['source_mask'].to(device, dtype = torch.long)

          generated_ids = model.generate(
              input_ids = ids,
              attention_mask = mask, 
              max_length=150, 
              num_beams=2,
              repetition_penalty=2.5, 
              length_penalty=1.0, 
              early_stopping=True
              )
          preds = [tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in generated_ids]
          target = [tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True)for t in y]
          if _%10==0:
              console.print(f'Completed {_}')

          predictions.extend(preds)
          actuals.extend(target)
  return predictions, actuals

In [15]:
def T5Trainer(dataframe, source_text, target_text, model_params, output_dir="./outputs/" ):
  
  """
  T5 trainer

  """

  # Set random seeds and deterministic pytorch for reproducibility
  torch.manual_seed(model_params["SEED"]) # pytorch random seed
  np.random.seed(model_params["SEED"]) # numpy random seed
  torch.backends.cudnn.deterministic = True

  # logging
  console.log(f"""[Model]: Loading {model_params["MODEL"]}...\n""")

  # tokenzier for encoding the text
  tokenizer = T5Tokenizer.from_pretrained(model_params["MODEL"])

  # Defining the model. We are using t5-base model and added a Language model layer on top for generation of Summary. 
  # Further this model is sent to device (GPU/TPU) for using the hardware.
  model = T5ForConditionalGeneration.from_pretrained(model_params["MODEL"])
  model = model.to(device)
  
  # logging
  console.log(f"[Data]: Reading data...\n")

  # Importing the raw dataset
  dataframe = dataframe[[source_text,target_text]]
  display_df(dataframe.head(2))

  
  # Creation of Dataset and Dataloader
  # Defining the train size. So 80% of the data will be used for training and the rest for validation. 
  train_size = 0.8
  train_dataset=dataframe.sample(frac=train_size,random_state = model_params["SEED"])
  val_dataset=dataframe.drop(train_dataset.index).reset_index(drop=True)
  train_dataset = train_dataset.reset_index(drop=True)

  console.print(f"FULL Dataset: {dataframe.shape}")
  console.print(f"TRAIN Dataset: {train_dataset.shape}")
  console.print(f"TEST Dataset: {val_dataset.shape}\n")


  # Creating the Training and Validation dataset for further creation of Dataloader
  training_set = YourDataSetClass(train_dataset, tokenizer, model_params["MAX_SOURCE_TEXT_LENGTH"], model_params["MAX_TARGET_TEXT_LENGTH"], source_text, target_text)
  val_set = YourDataSetClass(val_dataset, tokenizer, model_params["MAX_SOURCE_TEXT_LENGTH"], model_params["MAX_TARGET_TEXT_LENGTH"], source_text, target_text)


  # Defining the parameters for creation of dataloaders
  train_params = {
      'batch_size': model_params["TRAIN_BATCH_SIZE"],
      'shuffle': True,
      'num_workers': 0
      }


  val_params = {
      'batch_size': model_params["VALID_BATCH_SIZE"],
      'shuffle': False,
      'num_workers': 0
      }


  # Creation of Dataloaders for testing and validation. This will be used down for training and validation stage for the model.
  training_loader = DataLoader(training_set, **train_params)
  val_loader = DataLoader(val_set, **val_params)


  # Defining the optimizer that will be used to tune the weights of the network in the training session. 
  optimizer = torch.optim.Adam(params =  model.parameters(), lr=model_params["LEARNING_RATE"])


  # Training loop
  console.log(f'[Initiating Fine Tuning]...\n')

  for epoch in range(model_params["TRAIN_EPOCHS"]):
      train(epoch, tokenizer, model, device, training_loader, optimizer)
      
  console.log(f"[Saving Model]...\n")
  #Saving the model after training
  path = os.path.join(output_dir, "model_files")
  model.save_pretrained(path)
  tokenizer.save_pretrained(path)


  # evaluating test dataset
  console.log(f"[Initiating Validation]...\n")
  for epoch in range(model_params["VAL_EPOCHS"]):
    predictions, actuals = validate(epoch, tokenizer, model, device, val_loader)
    final_df = pd.DataFrame({'Generated Text':predictions,'Actual Text':actuals})
    final_df.to_csv(os.path.join(output_dir,'predictions.csv'))
  
  console.save_text(os.path.join(output_dir,'logs.txt'))
  
  console.log(f"[Validation Completed.]\n")
  console.print(f"""[Model] Model saved @ {os.path.join(output_dir, "model_files")}\n""")
  console.print(f"""[Validation] Generation on Validation data saved @ {os.path.join(output_dir,'predictions.csv')}\n""")
  console.print(f"""[Logs] Logs saved @ {os.path.join(output_dir,'logs.txt')}\n""")

In [16]:
model_params={
    "MODEL":"t5-small",             # model_type: t5-base/t5-large
    "TRAIN_BATCH_SIZE":8,          # training batch size
    "VALID_BATCH_SIZE":8,          # validation batch size
    "TRAIN_EPOCHS":3,              # number of training epochs
    "VAL_EPOCHS":1,                # number of validation epochs
    "LEARNING_RATE":1e-4,          # learning rate
    "MAX_SOURCE_TEXT_LENGTH":1024,  # max length of source text
    "MAX_TARGET_TEXT_LENGTH":200,   # max length of target text
    "SEED": 42                     # set seed for reproducibility 

}

In [22]:
T5Trainer(dataframe=df[:5000] ,source_text="text", target_text="summary", model_params=model_params, output_dir="outputs")

[05:11:38] [Model]: Loading t5-small...                                          <ipython-input-15-b1eef7f6be59>:14
                                                                                                                   

/usr/local/lib/python3.7/dist-packages/transformers/models/t5/tokenization_t5.py:174: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-small automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  FutureWarning,


[05:11:40] [Data]: Reading data...                                               <ipython-input-15-b1eef7f6be59>:25
                                                                                                                   

                                                    Sample Data                                                    
+-----------------------------------------------------------------------------------------------------------------+
|                      source_text                       |                       target_text                      |
|--------------------------------------------------------+--------------------------------------------------------|
|  summarize: A composite sketch of a man suspected of   |    – Just a week after 15-year-old Ruby Rubio got an   |
|stealing a teen's cellphone and causing her death when  |  iPhone and promised her mother she'd treat the prized |
|she was thrown off the trunk of the car he fled in was  |   possession with care, a mugger snatched it from the  |
|released by officials Tuesday. Vikki Vargas reports for |  girl while she was walking her 7-year-old sister home |
|  NBC4 News at 5 p.m. from Santa Ana Tuesday, July 8,   |   from school. The teen from Santa Ana, Calif., gave   |
|        2014. (Published Tuesday, July 8, 2014)         |  chase and managed to jump on top of the trunk of the  |
|                                                        |   getaway car, a gray or silver Pontiac that had been  |
|   A heartbroken family was pleading for the public's   |   waiting nearby, and hold on to the antenna, reports  |
|  help on Tuesday after a teenage girl died trying to   | KCAL9. But when the car swerved she was thrown off and |
|     stop a man who stole her iPhone, police said.      | hit her head. She suffered severe head trauma and died |
|                                                        |   at the hospital two days later, on Saturday. Though  |
| Ruby Rubio, 15, was walking with her 7-year-old sister |   police have yet to find the mugger, described as a   |
| on West Warner Avenue in Santa Ana on July 3 when she  |  5-foot 10-inch Hispanic man in his early 20s to early |
|  was confronted by a man, according to the Santa Ana   |  30s, the phone was recovered nearby; police think it  |
|                  Police Department.                    | was tossed from the car, NBC Los Angeles reports. What |
|                                                        | may have been Ruby's last word: "mom." Says her mother,|
| The man snatched her iPhone before he jumped into the  |  "She only opened her eyes, looked at me for like five |
|  passenger seat of a silver or gray Pontiac waiting    |   seconds and said 'mom' and that was the last word I  |
|                 nearby, police said.                   | heard from her." She says her daughter earned the phone|
|                                                        | by doing well in school, and that Ruby may have worried|
| Rubio had just gotten the iPhone one week earlier and  | her mom would be mad about the stolen phone since she'd|
|    promised her mother she would take care of it.      |  broken two other phones already, reports the New York |
|                                                        | Daily News. The teen is far from the first to die while|
| Rubio chased after the robber and jumped onto the car  |  trying to retrieve a cell phone: examples here, here, |
|  as it began to drive away, but she fell off and was   |                        and here.                       |
|             critically hurt, police said.              |                                                        |
|                                                        |                                                        |
|  "As they drove off, they swerved, she was hanging on  |                                                        |
| to the trunk," Santa Ana Police Cpl. Anthony Bertagna  |                                                        |
|  said. "She fell off, struck her head and that's how   |                                                        |
|                    this started."                     

FULL Dataset: (5000, 2)

...

Completed 120

[05:41:34] [Validation Completed.]                                               <ipython-input-15-b1eef7f6be59>:95
                                                                                                                   

[Model] Model saved @ outputs/model_files

[Validation] Generation on Validation data saved @ outputs/predictions.csv

[Logs] Logs saved @ outputs/logs.txt

In [19]:
outputs_test = model.generate(batch['input_ids'])
print(tokenizer.decode(outputs_test[2], skip_special_tokens=True))
opt = tokenizer.decode(batch['labels'][2], skip_special_tokens=True)
print(len(opt.split()))

NameError: ignored

In [25]:
output_df = pd.read_csv("/content/outputs/predictions.csv")


Unnamed: 0                                     Generated Text  \
0           0  Robert James Campbell's execution had been sch...   

                                         Actual Text  
0  – The nation's first execution since Oklahoma'...

In [39]:
output_df['Generated Text'][3]

'The accident happened at the intersection of 53rd and Main streets outside Main Elementary School around 2:30pm, just after school had let out for the day. Police now say 14 people were taken to local hospitals. Two victims were treated and then released, but two children remained hospitalized Wednesday night. One child was being held for observation overnight, and the other was listed in critical but stable condition. "He wouldn\'t want to hurt nobody," Carter\'s daughter tells KTLA. "He won\'t want to hurt nobody."'

In [40]:
output_df['Actual Text'][3]

'– Police say a 100-year-old driver plowed his Cadillac into a group of people near an elementary school in South Los Angeles this afternoon, injuring nine kids and two adults, reports AP. Four of the kids, ranging in age from 4 to 11, were in serious condition at a local hospital, reports KTLA-TV. Authorities identified the driver as Preston Carter, and the TV station (which has his age as 101) reports that he thinks his brakes failed. Carter was not injured in the crash.'

In [33]:
df['text']

25643    summarize: A composite sketch of a man suspect...
33096    summarize: Dave Chappelle is in the midst of a...
22256    summarize: Meeting Abstracts 2015 Annual Meeti...
18007    summarize: Story highlights An appeals court s...
35273    summarize: Funeral likened to hosting World Cu...
                               ...                        
23129    summarize: A German shepherd was rescued by po...
14251    summarize: Advertisement Continue reading the ...
19465    summarize: Netflix’s “Amanda Knox” opens with ...
11508    summarize: Steve Brill, founder of CourtTV and...
2696     summarize: When Manny Pacquiao entered the rin...
Name: text, Length: 14000, dtype: object

In [36]:
!pip install -q sumeval==0.2.2

     |████████████████████████████████| 80 kB 3.8 MB/s 
     |████████████████████████████████| 116 kB 31.0 MB/s 


In [37]:
from sumeval.metrics.rouge import RougeCalculator

rouge = RougeCalculator(stopwords=True, lang="en")

def rouge_calc(preds, targets):
    rouge_1 = [rouge.rouge_n(summary=preds[i],references=targets[i],n=1) for i in range(len(preds))]
    rouge_2 = [rouge.rouge_n(summary=preds[i],references=targets[i],n=2) for i in range(len(preds))]
    rouge_l = [rouge.rouge_l(summary=preds[i],references=targets[i]) for i in range(len(preds))]

    return {"Rouge_1": np.array(rouge_1).mean(),
            "Rouge_2": np.array(rouge_2).mean(),
            "Rouge_L": np.array(rouge_l).mean()}

In [41]:
prediction = list(output_df['Generated Text']) 
ground_truth = list(output_df['Actual Text'])

rouge_calc(prediction,ground_truth)

{'Rouge_1': 0.2666363510957817,
 'Rouge_2': 0.09842842422109195,
 'Rouge_L': 0.17593461678435884}

In [43]:
type(output_df['Generated Text'][0])

str